This notebook is for snapping of substations to lines

In [10]:
import os
import matplotlib.pyplot as plt 
import geopandas as gpd
import geoplot
import pandas as pd
import numpy as np
import pandas as pd
import hvplot.pandas

# Africa shape data

In [11]:
world = gpd.read_file(gpd.datasets.get_path('naturalearth_lowres'))
africa = world.query('continent == "Africa"')
nigeriaplot = world.query('name == "Nigeria"')
#world

# Power data

In [12]:
pathg = os.path.realpath("data/raw")+'/africa_all_raw_generators.geojson' # Generators are not required in base_network
paths = os.path.realpath("data/clean")+'/africa_all_buses_clean.geojson'
pathl = os.path.realpath("data/clean")+'/africa_all_lines_clean.geojson'

generators = gpd.read_file(pathg).set_crs(epsg=4326, inplace=True)
substations = gpd.read_file(paths).set_crs(epsg=4326, inplace=True)
lines = gpd.read_file(pathl).set_crs(epsg=4326, inplace=True)

In [13]:
generators

id tags.power       tags.generator:type  \
0      3.905330e+09  generator           horizontal_axis   
1      6.424707e+09  generator               gas_turbine   
2      7.781363e+09  generator               gas_turbine   
3      7.781384e+09  generator               gas_turbine   
4      7.859724e+09  generator                      None   
...             ...        ...                       ...   
11679  3.939517e+08  generator  solar_photovoltaic_panel   
11680  8.022333e+08  generator                      None   
11681  6.777180e+08  generator  solar_photovoltaic_panel   
11682  6.559265e+08  generator                      None   
11683  3.316870e+08  generator                      None   

      tags.generator:method tags.generator:source  \
0              wind_turbine                  wind   
1                combustion                   gas   
2                combustion                   gas   
3                combustion                   gas   
4                      None                 solar   
...                     ...                   ...   
11679          photovoltaic                 solar   
11680                  None                 solar   
11681          photovoltaic                 solar   
11682      run-of-the-river                 hydro   
11683                  None                  None   

      tags.generator:output:electricity  Type     Area   Country  \
0                                850 kW  Node      NaN   algeria   
1                                 24 MW  Node      NaN   algeria   
2                                   yes  Node      NaN   algeria   
3                                 23 MW  Node      NaN   algeria   
4                                  None  Node      NaN   algeria   
...                                 ...   ...      ...       ...   
11679                               yes   Way     30.0  zimbabwe   
11680                               yes   Way  13900.0  zimbabwe   
11681                               yes   Way    120.0  zimbabwe   
11682                              None   Way   1340.0  zimbabwe   
11683                              None   Way   4570.0  zimbabwe   

                         geometry  
0       POINT (-0.06089 28.46528)  
1        POINT (6.04965 31.78816)  
2        POINT (6.06035 31.67451)  
3        POINT (6.02240 31.76278)  
4        POINT (8.80251 28.67569)  
...                           ...  
11679  POINT (29.36049 -15.72306)  
11680  POINT (28.97580 -21.73421)  
11681  POINT (32.62666 -19.31132)  
11682  POINT (32.84422 -18.43013)  
11683  POINT (31.14201 -17.90030)  

[11684 rows x 10 columns]

In [14]:
lines_ng = lines[lines["country"] == "nigeria"]
substations_ng = substations[substations["tags_country"] == "nigeria"]
generators_ng = generators[generators["Country"] == "nigeria"]

In [15]:
# Redact data frames
#g_ = generators[['id', 'tags.power', 'geometry', 'Type', 'Country']]
b_ = substations[['bus_id', 'symbol', 'geometry', 'tags_country']]
b_.rename(columns={"tags_country": "country"}, inplace="true")
l_ = lines[['line_id', 'tag_type', 'geometry', 'country']] #lines
l_.rename(columns={"line_id": "id"}, inplace="true")

/home/matin/miniconda3/envs/pypsa/lib/python3.7/site-packages/pandas/core/frame.py:4449: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,


In [16]:
# NIGERIA AS TEST
b_ = b_[b_["country"] == "nigeria"]
l_ = l_[l_["country"] == "nigeria"]


In [17]:
b_

bus_id      symbol                  geometry  country
558  215459565-1  substation   POINT (6.65481 7.47203)  nigeria
559  215459565-2  substation   POINT (6.65481 7.47203)  nigeria
560  564429999-1  substation   POINT (8.27428 5.19074)  nigeria
561  565180232-1  substation   POINT (6.21769 7.54960)  nigeria
562  549391509-1  substation   POINT (3.37946 6.46849)  nigeria
..           ...         ...                       ...      ...
627  267122040-1  substation  POINT (12.39201 9.27096)  nigeria
628  267122040-2  substation  POINT (12.39201 9.27096)  nigeria
629  695826179-1  substation   POINT (4.60870 9.85654)  nigeria
630  695826179-2  substation   POINT (4.60870 9.85654)  nigeria
631  395182307-1  substation  POINT (9.34890 11.68994)  nigeria

[74 rows x 4 columns]

In [18]:
# https://gis.stackexchange.com/questions/48949/epsg-3857-or-4326-for-googlemaps-openstreetmap-and-leaflet
# EPSG 3857 for google maps projected coors

b_.to_crs("EPSG:3857", inplace=True) # Projecting from ESPG 4326 to 3857

pd.set_option('mode.chained_assignment',None) # Disable SetCopyWarning
l_.to_crs("EPSG:3857", inplace=True)
pd.reset_option("mode.chained_assignment") # Enable SetCopyWarning

In [19]:
b_.bounds # Get Non-Existant Bounding Box of Points
# (minx, miny, maxx, maxy) = (west, south, east, north) = 
# west: Lower-left X coordinate
# south: Lower-left Y coordinate
# east: Upper-right X coordinate
# north: Upper-right Y coordinate

minx          miny          maxx          maxy
558  7.408101e+05  8.341499e+05  7.408101e+05  8.341499e+05
559  7.408101e+05  8.341499e+05  7.408101e+05  8.341499e+05
560  9.210882e+05  5.786224e+05  9.210882e+05  5.786224e+05
561  6.921504e+05  8.428604e+05  6.921504e+05  8.428604e+05
562  3.761997e+05  7.216037e+05  3.761997e+05  7.216037e+05
..            ...           ...           ...           ...
627  1.379472e+06  1.036572e+06  1.379472e+06  1.036572e+06
628  1.379472e+06  1.036572e+06  1.379472e+06  1.036572e+06
629  5.130386e+05  1.102677e+06  5.130386e+05  1.102677e+06
630  5.130386e+05  1.102677e+06  5.130386e+05  1.102677e+06
631  1.040715e+06  1.310442e+06  1.040715e+06  1.310442e+06

[74 rows x 4 columns]

In [20]:
offset = 100
bbox = b_.bounds + [-offset, -offset, offset, offset]
bbox # bbox is a square with length 200m

minx          miny          maxx          maxy
558  7.407101e+05  8.340499e+05  7.409101e+05  8.342499e+05
559  7.407101e+05  8.340499e+05  7.409101e+05  8.342499e+05
560  9.209882e+05  5.785224e+05  9.211882e+05  5.787224e+05
561  6.920504e+05  8.427604e+05  6.922504e+05  8.429604e+05
562  3.760997e+05  7.215037e+05  3.762997e+05  7.217037e+05
..            ...           ...           ...           ...
627  1.379372e+06  1.036472e+06  1.379572e+06  1.036672e+06
628  1.379372e+06  1.036472e+06  1.379572e+06  1.036672e+06
629  5.129386e+05  1.102577e+06  5.131386e+05  1.102777e+06
630  5.129386e+05  1.102577e+06  5.131386e+05  1.102777e+06
631  1.040615e+06  1.310342e+06  1.040815e+06  1.310542e+06

[74 rows x 4 columns]

In [21]:
l_

id tag_type                                           geometry  \
4198  671376884-1     line  LINESTRING (509676.133 871177.890, 509701.013 ...   
4199  782531821-1     line  LINESTRING (953930.792 851579.415, 953872.460 ...   
4200  556551853-1     line  LINESTRING (760808.496 1115885.964, 760446.908...   
4201  565103749-1     line  LINESTRING (875370.579 984107.633, 875452.398 ...   
4202  460928690-1     line  LINESTRING (622420.747 723718.024, 622680.967 ...   
...           ...      ...                                                ...   
4643  564462592-1     line  LINESTRING (371306.896 793776.297, 371423.938 ...   
4644  574205131-1     line  LINESTRING (928284.417 565287.351, 928279.920 ...   
4645  671878396-1     line  LINESTRING (723444.231 692584.571, 723753.855 ...   
4646  553781958-1     line  LINESTRING (820066.521 647178.058, 820339.510 ...   
4647  564416596-1     line  LINESTRING (448063.711 843243.140, 448457.237 ...   

      country  
4198  nigeria  
4199  nigeria  
4200  nigeria  
4201  nigeria  
4202  nigeria  
...       ...  
4643  nigeria  
4644  nigeria  
4645  nigeria  
4646  nigeria  
4647  nigeria  

[450 rows x 4 columns]

In [22]:
hits = bbox.apply(lambda row: list(l_.sindex.intersection(row)), axis=1) # list of the lines that overlap that bounding box.
hits # Index of lines are not the Ids

558         [176, 334, 209]
559         [176, 334, 209]
560               [167, 74]
561         [440, 200, 427]
562                      []
               ...         
627    [292, 226, 156, 157]
628    [292, 226, 156, 157]
629                   [354]
630                   [354]
631               [53, 181]
Length: 74, dtype: object

In [23]:
with pd.option_context('display.max_rows', None, 'display.max_columns', None):
    display(pd.DataFrame.from_records([hits.apply(len).value_counts().to_dict()]).transpose())

0
1   20
3   14
2   10
4   10
5    5
7    3
8    3
0    2
6    2
10   2
11   2
9    1

In [24]:
# Flatten Hits
tmp = pd.DataFrame({
    # index of points table
    "pt_idx": np.repeat(hits.index, hits.apply(len)),
    # ordinal position of line - access via iloc later
    "line_i": np.concatenate(hits.values)
})
tmp

pt_idx  line_i
0       558   176.0
1       558   334.0
2       558   209.0
3       559   176.0
4       559   334.0
..      ...     ...
250     628   157.0
251     629   354.0
252     630   354.0
253     631    53.0
254     631   181.0

[255 rows x 2 columns]

In [25]:
tmp = tmp.join(l_.reset_index(drop=True), on="line_i")

tmp = tmp.join(b_.geometry.rename("point"), on="pt_idx")

# tmp = tmp.join(b_.reset_index(drop=True), on="pt_idx")

tmp = gpd.GeoDataFrame(tmp, geometry="geometry", crs=b_.crs)
tmp

pt_idx  line_i           id tag_type  \
0       558   176.0  215459549-1     line   
1       558   334.0  563722389-1     line   
2       558   209.0  267281680-1     line   
3       559   176.0  215459549-1     line   
4       559   334.0  563722389-1     line   
..      ...     ...          ...      ...   
250     628   157.0  383291012-2     line   
251     629   354.0  695826178-1     line   
252     630   354.0  695826178-1     line   
253     631    53.0  564399462-1     line   
254     631   181.0  395182289-1     line   

                                              geometry  country  \
0    LINESTRING (741070.225 834014.353, 740867.513 ...  nigeria   
1    LINESTRING (744178.666 836957.093, 744010.563 ...  nigeria   
2    LINESTRING (740664.789 833996.142, 740461.887 ...  nigeria   
3    LINESTRING (741070.225 834014.353, 740867.513 ...  nigeria   
4    LINESTRING (744178.666 836957.093, 744010.563 ...  nigeria   
..                                                 ...      ...   
250  LINESTRING (1362509.257 1040435.486, 1362738.7...  nigeria   
251  LINESTRING (513006.522 1102656.684, 512912.758...  nigeria   
252  LINESTRING (513006.522 1102656.684, 512912.758...  nigeria   
253  LINESTRING (1040693.425 1310440.590, 1040721.1...  nigeria   
254  LINESTRING (943677.220 1337665.315, 943902.520...  nigeria   

                               point  
0      POINT (740810.101 834149.927)  
1      POINT (740810.101 834149.927)  
2      POINT (740810.101 834149.927)  
3      POINT (740810.101 834149.927)  
4      POINT (740810.101 834149.927)  
..                               ...  
250  POINT (1379472.423 1036572.191)  
251   POINT (513038.647 1102676.744)  
252   POINT (513038.647 1102676.744)  
253  POINT (1040714.796 1310442.227)  
254  POINT (1040714.796 1310442.227)  

[255 rows x 7 columns]

In [26]:
tmp

pt_idx  line_i           id tag_type  \
0       558   176.0  215459549-1     line   
1       558   334.0  563722389-1     line   
2       558   209.0  267281680-1     line   
3       559   176.0  215459549-1     line   
4       559   334.0  563722389-1     line   
..      ...     ...          ...      ...   
250     628   157.0  383291012-2     line   
251     629   354.0  695826178-1     line   
252     630   354.0  695826178-1     line   
253     631    53.0  564399462-1     line   
254     631   181.0  395182289-1     line   

                                              geometry  country  \
0    LINESTRING (741070.225 834014.353, 740867.513 ...  nigeria   
1    LINESTRING (744178.666 836957.093, 744010.563 ...  nigeria   
2    LINESTRING (740664.789 833996.142, 740461.887 ...  nigeria   
3    LINESTRING (741070.225 834014.353, 740867.513 ...  nigeria   
4    LINESTRING (744178.666 836957.093, 744010.563 ...  nigeria   
..                                                 ...      ...   
250  LINESTRING (1362509.257 1040435.486, 1362738.7...  nigeria   
251  LINESTRING (513006.522 1102656.684, 512912.758...  nigeria   
252  LINESTRING (513006.522 1102656.684, 512912.758...  nigeria   
253  LINESTRING (1040693.425 1310440.590, 1040721.1...  nigeria   
254  LINESTRING (943677.220 1337665.315, 943902.520...  nigeria   

                               point  
0      POINT (740810.101 834149.927)  
1      POINT (740810.101 834149.927)  
2      POINT (740810.101 834149.927)  
3      POINT (740810.101 834149.927)  
4      POINT (740810.101 834149.927)  
..                               ...  
250  POINT (1379472.423 1036572.191)  
251   POINT (513038.647 1102676.744)  
252   POINT (513038.647 1102676.744)  
253  POINT (1040714.796 1310442.227)  
254  POINT (1040714.796 1310442.227)  

[255 rows x 7 columns]

In [27]:
# TODO : Convert to Google Maps CRS (2D)
tmp["snap_dist"] = tmp.geometry.distance(gpd.GeoSeries(tmp.point))

In [28]:
tmp

pt_idx  line_i           id tag_type  \
0       558   176.0  215459549-1     line   
1       558   334.0  563722389-1     line   
2       558   209.0  267281680-1     line   
3       559   176.0  215459549-1     line   
4       559   334.0  563722389-1     line   
..      ...     ...          ...      ...   
250     628   157.0  383291012-2     line   
251     629   354.0  695826178-1     line   
252     630   354.0  695826178-1     line   
253     631    53.0  564399462-1     line   
254     631   181.0  395182289-1     line   

                                              geometry  country  \
0    LINESTRING (741070.225 834014.353, 740867.513 ...  nigeria   
1    LINESTRING (744178.666 836957.093, 744010.563 ...  nigeria   
2    LINESTRING (740664.789 833996.142, 740461.887 ...  nigeria   
3    LINESTRING (741070.225 834014.353, 740867.513 ...  nigeria   
4    LINESTRING (744178.666 836957.093, 744010.563 ...  nigeria   
..                                                 ...      ...   
250  LINESTRING (1362509.257 1040435.486, 1362738.7...  nigeria   
251  LINESTRING (513006.522 1102656.684, 512912.758...  nigeria   
252  LINESTRING (513006.522 1102656.684, 512912.758...  nigeria   
253  LINESTRING (1040693.425 1310440.590, 1040721.1...  nigeria   
254  LINESTRING (943677.220 1337665.315, 943902.520...  nigeria   

                               point   snap_dist  
0      POINT (740810.101 834149.927)   89.948371  
1      POINT (740810.101 834149.927)  120.957396  
2      POINT (740810.101 834149.927)  211.579138  
3      POINT (740810.101 834149.927)   89.948371  
4      POINT (740810.101 834149.927)  120.957396  
..                               ...         ...  
250  POINT (1379472.423 1036572.191)  152.972614  
251   POINT (513038.647 1102676.744)   37.873807  
252   POINT (513038.647 1102676.744)   37.873807  
253  POINT (1040714.796 1310442.227)   13.261047  
254  POINT (1040714.796 1310442.227)   19.132301  

[255 rows x 8 columns]

In [29]:
tolerance = offset
# Discard any lines that are greater than tolerance from points
tmp = tmp.loc[tmp.snap_dist <= tolerance]
# Sort on ascending snap distance, so that closest goes to top
tmp = tmp.sort_values(by=["snap_dist"])



In [30]:
# group by the index of the points and take the first, which is the
# closest line 
closest = tmp.groupby("pt_idx").first()
# construct a GeoDataFrame of the closest lines
closest = gpd.GeoDataFrame(closest, geometry="geometry")

In [31]:
with pd.option_context('display.max_rows', None, 'display.max_columns', None):
    display(closest)

line_i           id tag_type  \
pt_idx                                 
558      176.0  215459549-1     line   
559      176.0  215459549-1     line   
560       74.0  564433188-1     line   
561      440.0  565183241-1     line   
563      257.0  671606176-1     line   
564      218.0  671878397-1     line   
565      248.0  564441300-1     line   
566      325.0  671606172-1     line   
567      293.0  782483200-1     line   
568      293.0  782483200-1     line   
569      274.0  696198028-1     line   
570      105.0  567076454-1     line   
573      382.0  671376895-1     line   
574      286.0  671606180-1     line   
575      129.0  575693157-1     line   
576      129.0  575693157-1     line   
577      425.0  107866854-1     line   
578      425.0  107866854-1     line   
581      295.0  575695611-1     line   
582      233.0  566748624-1     line   
583       76.0  565183239-1     line   
584        5.0  567543513-1     line   
587      136.0  564445778-1     line   
588      405.0  574205130-1     line   
589      405.0  574205130-1     line   
590       76.0  565183239-1     line   
591      370.0  547223813-1     line   
592        7.0  696199394-1     line   
593      425.0  107866854-1     line   
596      434.0  746582403-1     line   
599      117.0  862171471-1     line   
600      275.0  782531822-1     line   
601      275.0  782531822-1     line   
602      199.0  696041195-1     line   
603      299.0  671606218-1     line   
606       80.0  564453868-1     line   
607      220.0  564747983-1     line   
608       68.0  782483193-1     line   
609       68.0  782483193-1     line   
610      240.0  696219803-1     line   
611      236.0  541770058-1     line   
614      332.0  671606226-1     line   
615      332.0  671606226-1     line   
616       92.0  671878389-1     line   
617       53.0  564399462-1     line   
618      383.0  671606214-1     line   
619       91.0  564410484-2     line   
620       91.0  564410484-2     line   
621       41.0  481286426-1     line   
622      142.0  267205843-1     line   
623      255.0  655276484-1     line   
624      101.0  695834326-1     line   
626      409.0  565154370-1     line   
627      292.0  575575829-1     line   
628      292.0  575575829-1     line   
629      354.0  695826178-1     line   
630      354.0  695826178-1     line   
631       53.0  564399462-1     line   

                                                 geometry  country  \
pt_idx                                                               
558     LINESTRING (741070.225 834014.353, 740867.513 ...  nigeria   
559     LINESTRING (741070.225 834014.353, 740867.513 ...  nigeria   
560     LINESTRING (921173.094 578739.955, 921089.783 ...  nigeria   
561     LINESTRING (692132.808 842838.862, 692141.168 ...  nigeria   
563     LINESTRING (536778.722 1024899.256, 536766.933...  nigeria   
564     LINESTRING (731898.279 636866.453, 731845.435 ...  nigeria   
565     LINESTRING (376862.017 721979.978, 377135.518 ...  nigeria   
566     LINESTRING (533398.784 1021927.537, 533396.457...  nigeria   
567     LINESTRING (397562.121 722046.560, 397531.720 ...  nigeria   
568     LINESTRING (397562.121 722046.560, 397531.720 ...  nigeria   
569     LINESTRING (449568.239 831952.758, 449674.115 ...  nigeria   
570     LINESTRING (401855.280 889692.523, 401872.601 ...  nigeria   
573     LINESTRING (368736.251 768044.481, 368783.584 ...  nigeria   
574     LINESTRING (627193.581 702325.212, 627217.326 ...  nigeria   
575     LINESTRING (815034.001 563569.019, 815025.607 ...  nigeria   
576     LINESTRING (815034.001 563569.019, 815025.607 ...  nigeria   
577     LINESTRING (429137.784 822878.646, 429115.687 ...  nigeria   
578     LINESTRING (429137.784 822878.646, 429115.687 ...  nigeria   
581     LINESTRING (842565.370 508613.034, 842609.108 ...  nigeria   
582     LINESTRING (687815.760 1127959.733, 687806.131...  nigeria   
583     LINESTRING (708868.046 816549.303, 708852.216 ...  nigeria 

In [32]:
# Position of nearest point from start of the line
pos = closest.geometry.project(gpd.GeoSeries(closest.point))
# Get new point location geometry
new_pts = closest.geometry.interpolate(pos)

In [33]:
pos

pt_idx
558       250.565169
559       250.565169
560        85.675224
561         0.000000
563        31.609406
564         0.000000
565      5838.349311
566         0.000000
567       111.442894
568       111.442894
569     24629.091174
570         0.000000
573        59.907474
574        30.858219
575         0.000000
576         0.000000
577    102896.417182
578    102896.417182
581         0.000000
582         0.000000
583     70777.866710
584         0.000000
587        23.439308
588        60.127453
589        60.127453
590         0.000000
591       718.631067
592        23.597885
593         0.000000
596        93.017158
599         0.000000
600        13.033202
601        13.033202
602     93077.024853
603         4.758145
606         0.000000
607     47540.505946
608       150.752376
609       150.752376
610        70.312251
611         0.000000
614         0.000000
615         0.000000
616        73.497480
617    101932.513109
618       129.938150
619    271424.919817
620   

In [34]:
new_pts

pt_idx
558      POINT (740827.827 834061.743)
559      POINT (740827.827 834061.743)
560      POINT (921089.783 578719.969)
561      POINT (692132.808 842838.862)
563     POINT (536766.933 1024928.584)
564      POINT (731898.279 636866.453)
565      POINT (378027.184 727477.220)
566     POINT (533398.784 1021927.537)
567      POINT (397531.720 721939.344)
568      POINT (397531.720 721939.344)
569      POINT (462562.070 851616.259)
570      POINT (401855.280 889692.523)
573      POINT (368783.584 768007.759)
574      POINT (627207.739 702297.793)
575      POINT (815034.001 563569.019)
576      POINT (815034.001 563569.019)
577      POINT (509648.370 871071.598)
578      POINT (509648.370 871071.598)
581      POINT (842565.370 508613.034)
582     POINT (687815.760 1127959.733)
583      POINT (689849.846 751400.763)
584      POINT (538787.894 787476.961)
587      POINT (392345.145 745241.910)
588      POINT (928353.981 565084.613)
589      POINT (928353.981 565084.613)
590      POINT (70

In [35]:
#Identify the columns we want to copy from the closest line to the point, such as a line ID.
line_columns = 'line_i'
# Create a new GeoDataFrame from the columns from the closest line and new point geometries (which will be called "geometries")
snapped = gpd.GeoDataFrame(
closest[line_columns],geometry=new_pts)

points = b_

# Join back to the original points:
updated_points = points.drop(columns=["geometry"]).join(snapped)
# You may want to drop any that didn't snap, if so:
updated_points = updated_points.dropna(subset=["geometry"])

In [36]:
# updated_points.to_file('./updates_points.geojson', driver="GeoJSON")  # Generate GeoJson

# Map

In [45]:
# ax = geoplot.polyplot(nigeriaplot ,edgecolor='grey', alpha = 0.5, figsize=(20, 20))

# points.loc[points['country'] == 'nigeria'].plot(figsize=(20, 20),markersize=10, color='orange',alpha = 0.3, ax=ax)
# updated_points.loc[updated_points['country'] == 'nigeria'].plot(figsize=(20, 20),markersize=10, color='green',alpha = 0.3, ax=ax)
# # generators.loc[generators['country'] == 'nigeria'].plot(figsize=(20, 20),markersize=25, color='blue',alpha = 0.3, ax=ax)
# lines.loc[lines['country'] == 'nigeria'].plot(figsize=(20, 20),markersize=25, color='red',alpha = 0.3, ax=ax)


# #plt.savefig('africa_transmission_and substations_110.png')

In [44]:
# substation_df = pd.read_csv(
#     "./data/clean/africa_all_buses_clean.csv",
#     index_col=0
# )

# substation_df.hvplot.points(
#     'x',
#     'y',
#     geo=True,
#     size = substation_df["tags_area"]**(0.5)/10,
#     frame_height=500,
#     alpha=0.4,
#     tiles='CartoLight',
#     hover_cols=['bus_id'],
#     c='tags_country'
# ).opts(
#     active_tools=['pan', 'wheel_zoom']
# )

In [43]:
substations_ng.hvplot(
    geo=True,
    size = substations["tags_area"]**(0.5)/10,
    frame_height=750,
    alpha=0.4,
    tiles='CartoLight',
    hover_cols=['bus_id'],
    color = 'orange'  
) * lines_ng.hvplot(
    geo=True,
    alpha=0.4,
    hover_cols=['line_id']
) * generators_ng.hvplot(
    geo=True,
    alpha=0.4,
    color = 'green'
).opts(
    active_tools=['pan', 'wheel_zoom']
)

:Overlay
   .Tiles.I   :Tiles   [x,y]
   .Points.I  :Points   [Longitude,Latitude]   (_size,bus_id)
   .Path.I    :Path   [Longitude,Latitude]   (line_id)
   .Points.II :Points   [Longitude,Latitude]